In [2]:
from typing import List, Literal
import pandas as pd
from pandas import DataFrame
import numpy as np
from sklearn.metrics import mean_absolute_error
from lightgbm import LGBMRegressor
import joblib
from catboost import CatBoostRegressor
import json
import optuna
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [3]:
cleaned_dataset_address = "../dataset/interim/past_dataset.csv"

In [4]:
SEED = 87
TARGET = "general_dam_occupancy_rate"

In [5]:
try:
    with open("../models/best_features_by_lightgbm.json", errors="FileNotFoundError") as f:
        best_features = json.load(f)
        
except FileNotFoundError:
    best_features = []

In [6]:
past_knowledge = pd.read_csv(cleaned_dataset_address, parse_dates=["datetime"])
past_knowledge = past_knowledge.sort_values("datetime")

In [7]:
class FeatureExtractor:
    def __init__(
        self,
        past_knowledge: DataFrame,
        cyclical_feature_names: List[str],
        lag_size: int = 30,
        window_size: int = 30,
    ):
        self.PAST_KNOWLEDGE = past_knowledge.sort_values(by="datetime")
        self.cyclical_feature_names = cyclical_feature_names
        self.lag_size = lag_size
        self.window_size = window_size

    def transform(self, df: DataFrame) -> DataFrame:
        return (
            df.sort_values("datetime")
            .pipe(self._add_lag_features)
            .pipe(self._add_rolling_window_features)
            .pipe(self._add_exponential_moving_features)
            .pipe(self._drop_columns_with_same_values)
            .pipe(self._expand_datetime)
            .pipe(self._add_fourier_features)
            .pipe(
                lambda df: df.astype(
                    {col: "float32" for col in df.select_dtypes("number").columns}
                )
            )
            .bfill()
        )

    def _add_lag_features(
        self,
        df: DataFrame,
        fillna_with: Literal["ffill", "bfill"] | None = "bfill",
    ) -> DataFrame:
        df["datetime"] = pd.to_datetime(df["datetime"])

        df = df.sort_values("datetime")

        full_date_range = pd.date_range(
            start=self.PAST_KNOWLEDGE["datetime"].min(),
            end=df["datetime"].max(),
            freq="D",
        )
        full_df = pd.DataFrame({"datetime": full_date_range})
        full_df = full_df.merge(self.PAST_KNOWLEDGE, on="datetime", how="left")

        columns_to_use = self.PAST_KNOWLEDGE.select_dtypes(
            include="number"
        ).columns.tolist()

        created_features = []
        for col in columns_to_use:
            for i in range(1, self.lag_size + 1):
                created_col_name = f"{col}_lag_{i}"
                created_features.append(full_df[col].shift(i).rename(created_col_name))

        lags_df = pd.concat([full_df["datetime"], *created_features], axis=1)

        df = df.merge(
            lags_df,
            on="datetime",
            how="left",
        )

        if fillna_with == "ffill":
            df = df.ffill()
        elif fillna_with == "bfill":
            df = df.bfill()

        return df

    def _add_rolling_window_features(
        self,
        df: DataFrame,
        fillna_with: Literal["ffill", "bfill"] | None = "ffill",
    ) -> DataFrame:
        df["datetime"] = pd.to_datetime(df["datetime"])

        df = df.sort_values("datetime")

        full_date_range = pd.date_range(
            start=self.PAST_KNOWLEDGE["datetime"].min(),
            end=df["datetime"].max(),
            freq="D",
        )
        full_df = pd.DataFrame({"datetime": full_date_range}).merge(
            self.PAST_KNOWLEDGE, on="datetime", how="left"
        )

        columns_to_use = self.PAST_KNOWLEDGE.select_dtypes(
            include=["number"]
        ).columns.tolist()

        metrics = ["mean", "std", "min", "max", "median", "var"]

        created_features = []
        for col in columns_to_use:
            for size in range(2, self.window_size + 1):
                rolling_window_feature = (
                    full_df[col]
                    .rolling(window=size, min_periods=1)
                    .agg(metrics)
                    .rename(columns=lambda metric: f"{col}_rw{size}_{metric}")
                )
                created_features.append(rolling_window_feature)

        window_df = pd.concat([full_df["datetime"], *created_features], axis=1)

        df = df.merge(
            window_df,
            on="datetime",
            how="left",
        )

        if fillna_with == "ffill":
            df = df.ffill()
        elif fillna_with == "bfill":
            df = df.bfill()

        return df

    def _drop_columns_with_same_values(self, df: DataFrame, threshold=0.9) -> DataFrame:
        to_drop = [
            col
            for col in df.columns
            if df[col].value_counts(normalize=True, dropna=False).values[0] >= threshold
        ]
        return df.drop(columns=to_drop)

    def _add_exponential_moving_features(
        self, df: pd.DataFrame, up_to: int = 30
    ) -> pd.DataFrame:
        df["datetime"] = pd.to_datetime(df["datetime"])

        df = df.sort_values("datetime")

        full_date_range = pd.date_range(
            start=self.PAST_KNOWLEDGE["datetime"].min(),
            end=df["datetime"].max(),
            freq="D",
        )
        full_df = pd.DataFrame({"datetime": full_date_range}).merge(
            self.PAST_KNOWLEDGE, on="datetime", how="left"
        )

        columns_to_use = self.PAST_KNOWLEDGE.select_dtypes(
            include=["number"]
        ).columns.tolist()

        columns_to_use = self.PAST_KNOWLEDGE.select_dtypes(include="number").columns
        metrics = ["mean"]
        created_features = []

        for col in columns_to_use:
            for span in range(2, up_to + 1):
                feature = (
                    full_df[col]
                    .ewm(span=span, adjust=False)
                    .agg(metrics)
                    .rename(columns=lambda metric: f"{col}_em_{span}_{metric}")
                )
                created_features.append(feature)

        pd.concat([df, *created_features], axis=1)

        exponential_moving_df = pd.concat(
            [full_df["datetime"], *created_features], axis=1
        )

        df = df.merge(
            exponential_moving_df,
            on="datetime",
            how="left",
        )
        return df

    def _expand_datetime(self, df: DataFrame, column: str = "datetime") -> DataFrame:
        return df.assign(
            **{
                "year": lambda a_df: a_df[column].dt.year,
                "month": lambda a_df: a_df[column].dt.month,
                "day": lambda a_df: a_df[column].dt.day,
                "hour": lambda a_df: a_df[column].dt.hour,
                "day_of_year": lambda a_df: a_df[column].dt.dayofyear,
                "week_of_year": lambda a_df: a_df[column].dt.isocalendar().week,
                "quarter": lambda a_df: a_df[column].dt.quarter,
                # "season": lambda a_df: a_df[column].dt.month % 12 // 3 + 1,
                "is_weekend": lambda a_df: (a_df[column].dt.weekday >= 5).map(
                    {True: 1, False: 0}
                ),
            }
        )

    def _add_fourier_features(self, df: pd.DataFrame, num_terms: int = 7) -> DataFrame:
        for col, max_val in self.cyclical_feature_names.items():
            source = self._get_column_source(df, col)

            for i in range(1, num_terms + 1):
                operation = 2 * np.pi * i * source[col] / max_val

                df[f"fourier_sin_{col}_{i}"] = np.sin(operation)
                df[f"fourier_cos_{col}_{i}"] = np.cos(operation)

        return df

    def _get_column_source(self, df: DataFrame, col: str) -> List[str]:
        if col in df.columns:
            source = df
        elif col in self.PAST_KNOWLEDGE.columns:
            source = self.PAST_KNOWLEDGE
        else:
            raise KeyError(f"{col} not found both in df and past knowledge.")
        return source


In [8]:
parameters = {
    "past_knowledge": past_knowledge,
    "cyclical_feature_names": {
        "month": 12,
        "day": 31,
        "day_of_year": 365,
        "week_of_year": 52,
        "quarter": 4,
        # "season": 4,
        "is_weekend": 2,
        "precipitation_hours": 24,
    },
    "lag_size": 30,
    "window_size": 30,
}

In [9]:
feature_extractor = FeatureExtractor(**parameters)

In [10]:
known_dates = pd.DataFrame(past_knowledge["datetime"])

In [11]:
y_values = past_knowledge.loc[:, ["datetime", TARGET]]

In [12]:
X_values = feature_extractor.transform(known_dates).filter(items=["datetime", *best_features])

In [13]:
train_size = int(len(X_values) * 0.7)
val_size = int(len(X_values) * 0.15)

In [14]:
train_df = X_values.iloc[:train_size].merge(y_values, on="datetime", how="inner")

val_df = X_values.iloc[train_size : train_size + val_size].merge(
    y_values, on="datetime", how="inner"
)

test_df = X_values.iloc[train_size + val_size :].merge(
    y_values, on="datetime", how="inner"
)


In [15]:
X_train, y_train = (
    train_df.drop(columns=["datetime", "general_dam_occupancy_rate"]),
    train_df["general_dam_occupancy_rate"],
)

X_val, y_val = (
    val_df.drop(columns=["datetime", "general_dam_occupancy_rate"]),
    val_df["general_dam_occupancy_rate"],
)

X_test, y_test = (
    test_df.drop(columns=["datetime", "general_dam_occupancy_rate"]),
    test_df["general_dam_occupancy_rate"],
)


## Feature Selection

In [16]:
if len(best_features) == 0:
    lgb = LGBMRegressor(importance_type="gain", random_state=SEED)
    model = lgb.fit(X_train, y_train)
    feature_importance = {
        name: importance
        for name, importance in zip(model.feature_names_in_, model.feature_importances_)
    }
    number_of_features_to_select = round(len(X_train.columns) ** (1 / 2))
    best_columns = (
        pd.DataFrame(feature_importance, index=[0]).T.sort_values(0, ascending=False)[0:number_of_features_to_select].index.to_list()
    )
    with open("../models/best_features_by_lightgbm.json", "w") as f:
        json.dump(best_columns, f)

In [38]:
def objective(trial):
    params = {
        "learning_rate": trial.suggest_float("learning_rate", 0.0001, 0.1, log=True),
        "n_estimators": trial.suggest_int("n_estimators", 100, 1000),
        "max_depth": trial.suggest_int("max_depth", 3, 8),
        "l2_leaf_reg": trial.suggest_float("l2_leaf_reg", 0.1, 10.0, log=True),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.5, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 100),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "max_bin": trial.suggest_int("max_bin", 100, 500),
        "od_type": trial.suggest_categorical("od_type", ["IncToDec", "Iter"]),
        "random_strength": trial.suggest_float("random_strength", 0.0, 100.0),
        "leaf_estimation_method": trial.suggest_categorical(
            "leaf_estimation_method", ["Newton", "Gradient"]
        ),
        "grow_policy": trial.suggest_categorical(
            "grow_policy", ["SymmetricTree", "Depthwise", "Lossguide"]
        ),
        "feature_border_type": trial.suggest_categorical(
            "feature_border_type", ["GreedyLogSum", "MinEntropy", "Uniform"]
        ),
        "one_hot_max_size": trial.suggest_int("one_hot_max_size", 2, 10),
        "max_ctr_complexity": trial.suggest_int("max_ctr_complexity", 1, 8),
        "bagging_temperature": trial.suggest_float("bagging_temperature", 0.0, 1.0),
        "leaf_estimation_iterations": trial.suggest_int(
            "leaf_estimation_iterations", 1, 10
        ),
        "leaf_estimation_backtracking": trial.suggest_categorical(
            "leaf_estimation_backtracking", ["No", "AnyImprovement"]
        ),
        "random_score_type": trial.suggest_categorical(
            "random_score_type", ["NormalWithModelSizeDecrease", "Gumbel"]
        ),
    }

    model = CatBoostRegressor(**params, random_state=SEED, early_stopping_rounds=100)
    model.fit(X_train, y_train)
    y_pred = model.predict(X_val)

    dummy_forecaster_mae_error = 14.062895669528846

    return (
        mean_absolute_error(y_val, y_pred)
        if mean_absolute_error(y_val, y_pred) < dummy_forecaster_mae_error
        else float(np.inf)
    )


In [39]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=100, show_progress_bar=True, n_jobs=-1)
best_params = study.best_params

[I 2025-02-17 19:02:49,880] A new study created in memory with name: no-name-1410ba4b-d254-4dc1-8105-cdac75205d53


  0%|          | 0/100 [00:00<?, ?it/s]

0:	learn: 24.9496656	total: 14.8ms	remaining: 2.88s
0:	learn: 24.2143886	total: 7.37ms	remaining: 870ms
0:	learn: 24.9446771	total: 55.8ms	remaining: 31.6s
1:	learn: 23.8594581	total: 15.3ms	remaining: 893ms
2:	learn: 23.2633764	total: 35ms	remaining: 1.35s
3:	learn: 22.7014256	total: 41.6ms	remaining: 1.2s
1:	learn: 24.9478206	total: 69.1ms	remaining: 6.7s
2:	learn: 24.9455558	total: 86.3ms	remaining: 5.55s
4:	learn: 22.4366693	total: 65ms	remaining: 1.48s
5:	learn: 21.8541081	total: 71.3ms	remaining: 1.34s
3:	learn: 24.9432368	total: 118ms	remaining: 5.66s
6:	learn: 21.3663166	total: 96ms	remaining: 1.53s
0:	learn: 24.9395524	total: 123ms	remaining: 12.4s
7:	learn: 20.7819332	total: 103ms	remaining: 1.43s
8:	learn: 20.2056863	total: 112ms	remaining: 1.36s
1:	learn: 24.9383775	total: 184ms	remaining: 52s
9:	learn: 19.6866998	total: 142ms	remaining: 1.54s
4:	learn: 24.9409168	total: 186ms	remaining: 7.11s
10:	learn: 19.2010047	total: 174ms	remaining: 1.7s
1:	learn: 24.9270432	total: 20

In [76]:
best_params

{'learning_rate': 0.01813069428779062,
 'n_estimators': 863,
 'max_depth': 5,
 'l2_leaf_reg': 1.7958191080688655,
 'colsample_bylevel': 0.7993981849787956,
 'min_data_in_leaf': 96,
 'subsample': 0.5705997571695023,
 'max_bin': 397,
 'od_type': 'IncToDec',
 'random_strength': 0.014435490289824493,
 'leaf_estimation_method': 'Gradient',
 'grow_policy': 'Lossguide',
 'feature_border_type': 'MinEntropy',
 'one_hot_max_size': 10,
 'max_ctr_complexity': 5,
 'bagging_temperature': 0.8629206662618324,
 'leaf_estimation_iterations': 5,
 'leaf_estimation_backtracking': 'AnyImprovement',
 'random_score_type': 'Gumbel'}

In [67]:
model = CatBoostRegressor(**best_params, random_state=SEED, early_stopping_rounds=100)
model.fit(X_train, y_train)

0:	learn: 24.5002877	total: 6.48ms	remaining: 5.58s
1:	learn: 24.0575529	total: 12.7ms	remaining: 5.46s
2:	learn: 23.6229312	total: 18.6ms	remaining: 5.34s
3:	learn: 23.1960835	total: 24.5ms	remaining: 5.27s
4:	learn: 22.7772228	total: 30.2ms	remaining: 5.19s
5:	learn: 22.3657033	total: 36.1ms	remaining: 5.15s
6:	learn: 21.9617523	total: 42.1ms	remaining: 5.14s
7:	learn: 21.5651629	total: 47.9ms	remaining: 5.12s
8:	learn: 21.1757015	total: 53.7ms	remaining: 5.09s
9:	learn: 20.7930263	total: 59.5ms	remaining: 5.08s
10:	learn: 20.4174957	total: 65.7ms	remaining: 5.09s
11:	learn: 20.0485251	total: 71.8ms	remaining: 5.09s
12:	learn: 19.6864259	total: 77.8ms	remaining: 5.09s
13:	learn: 19.3306513	total: 83.8ms	remaining: 5.08s
14:	learn: 18.9811814	total: 90.8ms	remaining: 5.13s
15:	learn: 18.6383584	total: 98.7ms	remaining: 5.22s
16:	learn: 18.3017089	total: 106ms	remaining: 5.26s
17:	learn: 17.9711776	total: 113ms	remaining: 5.3s
18:	learn: 17.6466601	total: 119ms	remaining: 5.3s
19:	lear

{'learning_rate': 0.01813069428779062,
 'n_estimators': 863,
 'max_depth': 5,
 'l2_leaf_reg': 1.7958191080688655,
 'colsample_bylevel': 0.7993981849787956,
 'min_data_in_leaf': 96,
 'subsample': 0.5705997571695023,
 'max_bin': 397,
 'od_type': 'IncToDec',
 'random_strength': 0.014435490289824493,
 'leaf_estimation_method': 'Gradient',
 'grow_policy': 'Lossguide',
 'feature_border_type': 'MinEntropy',
 'one_hot_max_size': 10,
 'max_ctr_complexity': 5,
 'bagging_temperature': 0.8629206662618324,
 'leaf_estimation_iterations': 5,
 'leaf_estimation_backtracking': 'AnyImprovement',
 'random_score_type': 'Gumbel'}

In [68]:
joblib.dump(model, "../models/catboost-1.pkl.gz", compress="gzip")

['../models/catboost-1.pkl.gz']

In [69]:
train_pred = model.predict(X_train)
mean_absolute_error(y_train, train_pred)

0.058644801110443644

In [70]:
val_pred = model.predict(X_val)

In [71]:
mean_absolute_error(y_val, val_pred)

0.09630055656967536

In [72]:
test_pred = model.predict(X_test)

In [73]:
mean_absolute_error(y_test, test_pred)

0.3261406422763714

In [74]:
train_pred = pd.concat([train_df["datetime"], pd.Series(train_pred, name="predictions"), y_train], axis=1)
val_pred = pd.concat([val_df["datetime"], pd.Series(val_pred, name="predictions"), y_val], axis=1)
test_pred = pd.concat([test_df["datetime"], pd.Series(test_pred, name="predictions"), y_test], axis=1)

In [75]:
fig = make_subplots(rows=1, cols=3, subplot_titles=("Train", "Validation", "Test"))

for i, (df, name) in enumerate(zip([train_pred, val_pred, test_pred], ["Train", "Validation", "Test"])):
    fig.add_trace(go.Scatter(x=df.datetime, y=df[TARGET], mode="lines", name=f"{name} True"), row=1, col=i+1)
    fig.add_trace(go.Scatter(x=df.datetime, y=df["predictions"], mode="lines", name=f"{name} Predictions"), row=1, col=i+1)

fig.update_layout(height=400, width=1200, title_text="Predictions vs. True Values")
fig.show()
